In [1]:
import nltk;
import string
import sys
import pandas as pd
import networkx as nx
import sklearn.decomposition as dec
import sklearn.manifold as manif
import matplotlib.pyplot as plt
import mpld3
import scipy.sparse.linalg as linalg
import numpy as np
import sympy as sp
import matplotlib.pyplot as plt
import time
import json
import glob
import re
import os
import itertools 
import pickle

In [2]:
from nltk.stem import WordNetLemmatizer
from nltk import sent_tokenize, word_tokenize, pos_tag, wordnet
from summa import keywords
from summa.summarizer import summarize
from nltk.tokenize import MWETokenizer
from pybabelfy.babelfy import *
from nltk.corpus import stopwords
from pybabelnet.babelnet import BabelNet
from unidecode import unidecode    
from collections import OrderedDict
#from nltk.stem import PorterStemmer
from porterStemmer import PorterStemmer
from math import log


In [3]:
def openFile(fileName):
    file = open(fileName,"r") 
    text = file.read() 
    file.close()
    return text

In [4]:
def parseText(texto):
    text = ""
    punctuation = string.punctuation
    punctuation = punctuation.replace('!','')
    punctuation = punctuation.replace('.','')
    punctuation = punctuation.replace('?','')
    punctuation = punctuation.replace('-','')
    translator = str.maketrans('', '', punctuation)
    
    for l in texto.splitlines():
        printable = "".join(filter(str.isprintable,l))
        text = text + '\n' + printable.translate(translator)
    text = unidecode(text)
    text = text.replace('%','')
    text = re.sub(r'[0-9]+', '', text)
    text = re.sub(r'  ', ' ', text)
    splitted_text = [s.strip() for s in text.splitlines()]
    new_splitted_text = []
    punctuation = ['.','?','!']
    new_splitted_text.append("")
    for line in text.splitlines():
        if new_splitted_text[-1][-1:] not in punctuation or len(new_splitted_text[-1] + line) <= 3000: 
            new_splitted_text[-1] = new_splitted_text[-1] + ' ' + line
        else:
            new_splitted_text.append(line)
    translator = str.maketrans('', '', "?!.")
    for l in new_splitted_text:
        l = l.translate(translator)
    return new_splitted_text

In [5]:
def frag(semantic_annotation, input_text):
    start = semantic_annotation.char_fragment_start()
    end = semantic_annotation.char_fragment_end()
    return input_text[start:end+1]

In [6]:
def babelfy(lang, KEY, splitted_text):
    babelapi = Babelfy()
    bn = BabelNet(key)
    paragraphs_annotations = []
    paragraphs_text = []
    paragraphs_code = []
    
    count = 0
    for paragraph in splitted_text: #annotate each paragraph
        words_annotations = []
        words_text = []
        words_code = []
        semantic_annotations = babelapi.disambiguate(paragraph,lang,key,match="EXACT_MATCHING",cands="TOP",mcs="ON",anntype="ALL")
        
        for semantic_annotation in semantic_annotations: #exclude unused annotations (multiword expressions)
            # primeira palavra ou  palavra atual comeca apos anteior
            if len(words_annotations) == 0 or words_annotations[-1].char_fragment_end() < semantic_annotation.char_fragment_start():
                words_annotations.append(semantic_annotation)
                #words_text.append(bn.getSynsets(semantic_annotation.babel_synset_id())[0].senses[0].properties.fullLemma.lower())
                words_text.append(frag(semantic_annotation,paragraph))
                words_code.append(semantic_annotation.babel_synset_id())

            # palavra atual comeca junto da palavra anterior
            elif words_annotations[-1].char_fragment_start() == semantic_annotation.char_fragment_start():
                del words_annotations[-1]
                words_annotations.append(semantic_annotation)
                del words_text[-1]
                #words_text.append(semantic_annotation.babel_synset_id())[0].senses[0].properties.fullLemma.lower())
                words_text.append(frag(semantic_annotation,paragraph))
                del words_code[-1]
                words_code.append(semantic_annotation.babel_synset_id())


        paragraphs_annotations.append(words_annotations)
        paragraphs_text.append(words_text)
        paragraphs_code.append(words_code)
        count = count + 1
        print(count)
        
    return paragraphs_annotations, paragraphs_text, paragraphs_code    

In [7]:
def saveText(file, paragraphs_code):
    file = open(file,"w+") 
    for p in paragraphs_code:
        for w in p:
            file.write(w + "#")
        file.write("\n")
    file.close()

 ## dicionario[palavra] = codigo
 ## dicionarioCode[codigo] = palavra
 ## peso[codigo] = peso

In [8]:
def createDicts(paragraphs_text, paragraphs_code):
    dicionario={}
    peso={}
    dicionarioCode={}
    for paragraph, codes in zip(paragraphs_text, paragraphs_code):
        for word, code in zip(paragraph, codes):
            if code not in peso or word not in dicionario:
                dicionario[word] = code
                peso[code] = 1
                if code not in dicionarioCode:
                    dicionarioCode[code] = word
            else:
                peso[code] = peso[code] + 1   
    return dicionario, dicionarioCode, peso

In [9]:
def createGraph(peso, paragraphs_code, dist):
    g = nx.DiGraph()
    g2 = nx.DiGraph()
    g3 = nx.DiGraph()
    for code, weight in peso.items():
        g.add_node(code, peso=weight)
        g2.add_node(code, peso=weight)
        g3.add_node(code, peso=weight)
    for line in paragraphs_code:
        i = 0
        for word in line:
            i = i + 1
            j = 0
            for word2 in line:
                j = j + 1
                if j - i < dist and j - i > 0:
                    if g.has_edge(word, word2):
                        #g[word][word2]['weight'] += 1/(j-i)
                        g[word][word2]['weight'] += 1 - log(j-i,dist)
                    else:
                        if word != word2:
                            #g.add_edge(word, word2, weight=float(1/(j-i)))
                            g.add_edge(word, word2, weight=float(1 - log(j-i,dist)))
                            #g.add_edge(word, word2, weight=float(log(dist/j-i,10)))
                if j - i == 1:
                    if g2.has_edge(word, word2):
                        g2[word][word2]['weight'] += 1
                    else:
                        if word != word2:
                            g2.add_edge(word, word2, weight=1)
                if j - i == 2:
                    if g3.has_edge(word, word2):
                        g3[word][word2]['weight'] += 1
                    else:
                        if word != word2:
                            g3.add_edge(word, word2, weight=1)
    ## Normalize edge weights
    #arcs = 0
    #for n1, n2, w in list(g.edges(data='weight')):
    #    arcs = arcs + w
    #for a in list(g.edges(data='weight')):
    #    g[n1][n2]['weight'] = g[n1][n2]['weight'] * 100 / arcs 

    return g, g2, g3
    

In [10]:
def nodeRank(g,dicionarioCode):
    #pr = nx.pagerank(g, weight='weight')
    #pr = nx.eigenvector.eigenvector_centrality_numpy(g, weight='weight')
    #pr = nx.closeness_centrality(g, distance='weight')
    pr = nx.degree_centrality(g)
    desc = sorted(pr.keys(), key=pr.get,reverse=False)
    pageRank = {}
    for p in pr:
        pageRank[p] = pr[str(p)] 
    pageRank = sorted(pageRank.items(), key=lambda kv: (kv[1], kv[0]), reverse=True)
    return pageRank

    #desc = sorted(pr.keys(), key=pr.get,reverse=False)
    #pageRank = {}
    #for p in pr:
    #    pageRank[dicionarioCode[p]] = pr[str(p)] 
    #pageRank = sorted(pageRank.items(), key=lambda kv: (kv[1], kv[0]), reverse=True)
    #return pageRank

In [11]:
def sortGraphs(graphs):
    newGraphs={}
    for name, g in graphs.items():
        if len(name) == 3:
            newName = name[:-1] + "0" +name[-1] 
            newGraphs[newName] = g
        else:
            newGraphs[name] = g

    newGraphs = OrderedDict(sorted(newGraphs.items()))

    graphs={}
    for name, g in newGraphs.items():
        if name[2] == '0':
            newName = name.replace("0", '')
            graphs[newName] = g
        else:
            graphs[name] = g
    return graphs

In [12]:
def saveKeyWords(keyWords, graphName, resultFile):
    file = open(resultFile,"w+") 
    stemmer=PorterStemmer()
    for words, name in zip(keyWords, graphName):
        file.write(name + " : ")
        #for word in [it[0] for it in nltk.pos_tag([item[0] for item in words]) if it[1] != 'VBN'][:15]:
        for word, weight, weight2 in words[:15]:
            parsedPhrase = ''
            count = 0
            for w in word.split(' '):
                if w != '':
                    parsedWord = stemmer.stem(w.lower())
                    count = count + 1
                    if count > 1:
                        parsedPhrase = parsedPhrase + ' ' + parsedWord
                    else:
                        parsedPhrase = parsedWord

            if(word != words[0][0]):
                file.write("," + parsedPhrase)
            else:
                file.write(parsedPhrase)
        file.write("\n")
    file.close()
    return 

In [13]:
def numericalSort(value):
    numbers = re.compile(r'(\d+)')
    parts = numbers.split(value)
    parts[1::2] = map(int, parts[1::2])
    return parts

In [14]:
def takeSecond(elem):
    return elem[1]

In [15]:
def keyPhrasesCompilation(keyWords, g, g2, dicionarioCode):
    key2 = {code : value for code, value in keyWords}
    
    keyphrases_all = []
    for k in keyWords[:20]:
        for k2 in keyWords[:20]:
            if k[0] != k2[0]:
                if g2.has_edge(k[0], k2[0]):
                    if g2.has_edge(k2[0], k[0]) and g2[k2[0]][k[0]]['weight'] > g2[k[0]][k2[0]]['weight']:
                        weight = g.out_degree(k2[0], weight='weight') + g.in_degree(k[0], weight='weight')
                        phrase = [k2[0] + ',' + k[0], g2[k2[0]][k[0]]['weight'], g[k2[0]][k[0]]['weight'] / weight]
                    else:
                        weight = g.out_degree(k[0], weight='weight') + g.in_degree(k2[0], weight='weight')
                        phrase = [k[0] + ',' + k2[0], g2[k[0]][k2[0]]['weight'], g[k[0]][k2[0]]['weight'] / weight]
                    if phrase not in keyphrases_all:
                        keyphrases_all.append(phrase)
                        
                        
    keyphrases_weight = [t[2] for t in keyphrases_all if t[1] >= 1]   # only phrases that appeared more than 2 times
    keyphrases_weight_norm = [float(i)/sum(keyphrases_weight) for i in keyphrases_weight]
    keyphrases = [t for t in keyphrases_all if t[1] >= 5]
    
    for kp, n in zip(keyphrases, keyphrases_weight_norm):
        codes = kp[0].split(',')
        #kp[1] = ((key2[codes[0]] + key2[codes[1]] ) / 2 ) / ((1-(n/(peso[0][codes[0]] * peso[0][codes[1]]))) / 1)
        #kp[1] = ((key2[codes[0]] + key2[codes[1]] ) / 2 ) / ((1-(n)) / 1)
        kp[1] = ((key2[codes[0]] + key2[codes[1]]) / 2) + n/2
        #kp[1] = n
        kp[0] = dicionarioCode[codes[0]] + ' ' + dicionarioCode[codes[1]]
        
    
    keywords = [[dicionarioCode[k[0]], k[1], 1] for k in keyWords]
    merged = keyphrases + keywords
    merged.sort(key=takeSecond, reverse=True)
        
    return merged

## Set variables

In [16]:
inputDirectory = "/home/mauro/Downloads/testeSemeval"
outputFile = "/home/mauro/Downloads/testeSemeval/teste.txt"
saveFile = "/home/mauro/Downloads/testeSemeval/teste2.txt"
resultFile = "/home/mauro/Downloads/testeSemeval/resultado.txt"

In [17]:
lang = "EN"
key = "3e33574f-d481-41ae-82f1-0a7caf846dd3" 

In [18]:
dist = 35
#dist  = float("inf")
#dist = 2

## Create graphs

In [19]:
#splitted_text = []
#dicionario = []
#dicionarioCode = []
#peso = []
#paragraphs_annotations = []
#paragraphs_text = []
#paragraphs_code = []
#graphName = []
graphs = []
graphs2 = []
keyWords = []
keyPhrases = []

## Save KeyWords

In [20]:
saveKeyWords(keyPhrases, graphName, resultFile)

NameError: name 'graphName' is not defined

In [21]:
def nodeRank(g,dicionarioCode):
    #pr = nx.pagerank(g, weight='weight')
    #pr = nx.eigenvector.eigenvector_centrality_numpy(g, weight='weight')
    #pr = nx.closeness_centrality(g, distance='weight')
    #pr = nx.betweenness_centrality(g, weight='weight')
    pr = nx.degree_centrality(g)
    desc = sorted(pr.keys(), key=pr.get,reverse=False)
    pageRank = {}
    for p in pr:
        pageRank[p] = pr[str(p)] 
    pageRank = sorted(pageRank.items(), key=lambda kv: (kv[1], kv[0]), reverse=True)
    return pageRank

    #desc = sorted(pr.keys(), key=pr.get,reverse=False)
    #pageRank = {}
    #for p in pr:
    #    pageRank[dicionarioCode[p]] = pr[str(p)] 
    #pageRank = sorted(pageRank.items(), key=lambda kv: (kv[1], kv[0]), reverse=True)
    #return pageRank

In [22]:
#Permite respostas iguais
def saveKeyWords(keyWords, graphName, resultFile):
    file = open(resultFile,"w+") 
    stemmer=PorterStemmer()
    for words, name in zip(keyWords, graphName):
        file.write(name + " : ")
        #for word in [it[0] for it in nltk.pos_tag([item[0] for item in words]) if it[1] != 'VBN'][:15]:
        for word, weight, weight2 in words[:15]:
            parsedPhrase = ''
            count = 0
            for w in word.split(' '):
                if w != '':
                    parsedWord = stemmer.stem(w.lower(), 0, len(w)-1)
                    count = count + 1
                    if count > 1:
                        parsedPhrase = parsedPhrase + ' ' + parsedWord
                    else:
                        parsedPhrase = parsedWord

            if(word != words[0][0]):
                file.write("," + parsedPhrase)
            else:
                file.write(parsedPhrase)
        file.write("\n")
    file.close()
    return 

In [23]:
#Permite respostas iguais
def saveKeyWords(keyWords, graphName, resultFile):
    file = open(resultFile,"w+") 
    stemmer=PorterStemmer()
    for words, name in zip(keyWords, graphName):
        file.write(name + " : ")
        #for word in [it[0] for it in nltk.pos_tag([item[0] for item in words]) if it[1] != 'VBN'][:15]:
        for word, weight, weight2 in words[:15]:
            parsedPhrase = ''
            for wr in word.split(' '):
                for w,i in zip(wr.split('-'),range(len(wr.split('-')))):
                    if w != '':
                        parsedWord = stemmer.stem(w.lower(), 0, len(w)-1)
                        if i >= 1:
                            parsedPhrase = parsedPhrase + '-' + parsedWord
                        else:
                            parsedPhrase = parsedPhrase + parsedWord
                
                parsedPhrase = parsedPhrase + ' '
            parsedPhrase = parsedPhrase[:len(parsedPhrase)-1]
            parsedPhrase = parsedPhrase.replace('  ',' ')
            
            if(word != words[0][0]):
                file.write("," + parsedPhrase)
            else:
                file.write(parsedPhrase)
        file.write("\n")
    file.close()
    return 

In [24]:
# Elimina respostas iguais (piora resultado)

def saveKeyWords(keyWords, graphName, resultFile):
    file = open(resultFile,"w+") 
    stemmer=PorterStemmer()
    for words, name in zip(keyWords, graphName):
        file.write(name + " : ")
        #for word in [it[0] for it in nltk.pos_tag([item[0] for item in words]) if it[1] != 'VBN'][:15]:
        keys = set()
        for word, weight, weight2 in words[:30]:
            parsedPhrase = ''
            for wr in word.split(' '):
                for w,i in zip(wr.split('-'),range(len(wr.split('-')))):
                    if w != '':
                        parsedWord = stemmer.stem(w.lower(), 0, len(w)-1)
                        if i >= 1:
                            parsedPhrase = parsedPhrase + '-' + parsedWord
                        else:
                            parsedPhrase = parsedPhrase + parsedWord
                parsedPhrase = parsedPhrase + ' '
            parsedPhrase = parsedPhrase[:len(parsedPhrase)-1]
            parsedPhrase = parsedPhrase.replace('  ',' ')  
            if parsedPhrase not in keys:
                keys.add(parsedPhrase)

                if(word != words[0][0]):
                    file.write("," + parsedPhrase)
                else:
                    file.write(parsedPhrase)
        file.write("\n")
    file.close()
    return 

In [25]:
def defineEdgeWeight(B, G, g):
    weightInB = 0.0
    #weightOutB = 0.0
    
    for u in B:
        for v in G:
            if g.has_edge(u, v):
                weightInB = weightInB + g[u][v]['weight'] 
          #  if g.has_edge(v, u):
          #      weightOutB = weightOutB + g[v][u]['weight']
    return weightInB

In [26]:
def mergeNodes(g1,g2,dicionarioCode):
    
    stemmer=PorterStemmer()
    #regra para união dos vértices (devem ter o mesmo radical)
    same_stem = lambda u, v: (stemmer.stem(dicionarioCode[u].lower(), 0, len(dicionarioCode[u])-1) == stemmer.stem(dicionarioCode[v].lower(), 0, len(dicionarioCode[v])-1))
    
    #regra do peso das uniões (soma de todos os vértices)
    node_weight = lambda G: {'peso' : (sum([g1.nodes[i]['peso'] for i in G]))}
    node_weight2 = lambda G: {'peso' : (sum([g2.nodes[i]['peso'] for i in G]))}
    
    #regra do peso das arestas (soma de todas as arestas)
    edges_weight = lambda B, G: {'weight' : (defineEdgeWeight(B, G, g1))}
    edges_weight2 = lambda B, G: {'weight' : (defineEdgeWeight(B, G, g2))}
    
        
    #merge nodes
    gra1 = nx.quotient_graph(g1,same_stem,node_data=node_weight, edge_data=edges_weight)
    gra2 = nx.quotient_graph(g2,same_stem,node_data=node_weight2, edge_data=edges_weight2)
    
    
    
    #atualiza nome dos vertices
    mappingNodes = {}
    for b in gra1.nodes():
        higherNode = ''
        higherWeight = 0
        for n in b:
            if g1.nodes[n]['peso'] > higherWeight:
                higherWeight = g1.nodes[n]['peso']
                higherNode = n
        mappingNodes[b] = higherNode
        
    grafo1 = nx.relabel_nodes(gra1, mappingNodes)
    
    mappingNodes = {}
    for b in gra2.nodes():
        higherNode = ''
        higherWeight = 0
        for n in b:
            if g2.nodes[n]['peso'] > higherWeight:
                higherWeight = g2.nodes[n]['peso']
                higherNode = n
        mappingNodes[b] = higherNode
        
    grafo2 = nx.relabel_nodes(gra2, mappingNodes)
    
    
    
    return grafo1,grafo2

In [27]:
#Permite respostas iguais
def saveKeyWords(keyWords, graphName, resultFile):
    file = open(resultFile,"w+") 
    stemmer=PorterStemmer()
    for words, name in zip(keyWords, graphName):
        file.write(name + " : ")
        #for word in [it[0] for it in nltk.pos_tag([item[0] for item in words]) if it[1] != 'VBN'][:15]:
        for word, weight, weight2 in words[:15]:
            parsedPhrase = ''
            for wr in word.split(' '):
                for w,i in zip(wr.split('-'),range(len(wr.split('-')))):
                    if w != '':
                        parsedWord = stemmer.stem(w.lower(), 0, len(w)-1)
                        if i >= 1:
                            parsedPhrase = parsedPhrase + '-' + parsedWord
                        else:
                            parsedPhrase = parsedPhrase + parsedWord
                
                parsedPhrase = parsedPhrase + ' '
            parsedPhrase = parsedPhrase[:len(parsedPhrase)-1]
            parsedPhrase = parsedPhrase.replace('  ',' ')
            
            if(word != words[0][0]):
                file.write("," + parsedPhrase)
            else:
                file.write(parsedPhrase)
        file.write("\n")
    file.close()
    return 

In [28]:
def createDicts(paragraphs_text, paragraphs_code):
    dicionario={}
    peso={}
    dicionarioCode={}
    for paragraph, codes in zip(paragraphs_text, paragraphs_code):
        for word, code in zip(paragraph, codes):
            if code not in peso:
                peso[code] = 1
            else:
                peso[code] = peso[code] + 1
                
            if word not in dicionario:
                    dicionario[word] = code
            if code not in dicionarioCode:
                    dicionarioCode[code] = word
            #elif len(dicionarioCode[code]) < len(word):
            #    dicionarioCode[code] = word
    return dicionario, dicionarioCode, peso

In [29]:
#Permite respostas iguais
def saveKeyWords(keyWords, graphName, resultFile):
    file = open(resultFile,"w+") 
    stemmer=PorterStemmer()
    for words, name in zip(keyWords, graphName):
        file.write(name + " : ")
        #for word in [it[0] for it in nltk.pos_tag([item[0] for item in words]) if it[1] != 'VBN'][:15]:
        for word, weight, weight2 in words[:15]:
            parsedPhrase = ''
            for wr in word.split(' '):
                for w,i in zip(wr.split('-'),range(len(wr.split('-')))):
                    if w != '':
                        parsedWord = stemmer.stem(w.lower(), 0, len(w)-1)
                        if i >= 1:
                            parsedPhrase = parsedPhrase + '-' + parsedWord
                        else:
                            parsedPhrase = parsedPhrase + parsedWord
                
                parsedPhrase = parsedPhrase + ' '
            parsedPhrase = parsedPhrase[:len(parsedPhrase)-1]
            parsedPhrase = parsedPhrase.replace('  ',' ')
            
            if(word != words[0][0]):
                file.write("," + parsedPhrase)
            else:
                file.write(parsedPhrase)
        file.write("\n")
    file.close()
    return 

In [30]:
def stemListOfWords(lists):
    stemmer=PorterStemmer()
    stemmedResults = []
    
    for l in lists:
        newWp = []
        for wp in l:
            newW = ''
            for w,i in zip(wp.split(' '), range(len(wp.split(' ')))):
                parsedWord = stemmer.stem(w.lower(), 0, len(w)-1)
                newW = newW + " " + parsedWord
            newW = newW[1:]
            newWp.append(newW)
        stemmedResults.append(newWp)
    return stemmedResults

In [31]:
a = [2,3,5]
b = [7,8,9]
c = a + b
c

[2, 3, 5, 7, 8, 9]

In [32]:
def openResults():
    inputDirectory = "/home/mauro/Downloads/Hulth2003/Test/Uncontr/"
    inputDirectory2 = "/home/mauro/Downloads/Hulth2003/Test/Contr/"
    results = []
    results2 = []

    for filename in sorted(glob.glob(os.path.join(inputDirectory, '*.uncontr')), key=numericalSort):
        text = openFile(filename)
        text = text.split(';')
        result = []
        for t in text:
            t = t.replace('\n', '')
            t = t.replace('\t', ' ')
            if t[0] == ' ':
                t = t[1:]
            if t[:len(t)] == ' ':
                t = t[:-1]
            result.append(t)
        results.append(result)
    
    for filename in sorted(glob.glob(os.path.join(inputDirectory2, '*.contr')), key=numericalSort):
        text = openFile(filename)
        text = text.split(';')
        result = []
        for t in text:
            t = t.replace('\n', '')
            t = t.replace('\t', ' ')
            if t[0] == ' ':
                t = t[1:]
            if t[:len(t)] == ' ':
                t = t[:-1]
            result.append(t)
        results2.append(result)
    
    finalResults = []
    for r, r2 in zip(results, results2):
        finalResults.append(r + r2)
    
    return results
        

In [33]:
openResults()

[['wavelength services',
  'fiber optic networks',
  'Looking Glass Networks',
  'PointEast Research'],
 ['telecom',
  'competitive carrier market',
  'NuVox Communications',
  'investors'],
 ['telecom industry', 'insider investment'],
 ['robust stabilization',
  'adaptive stabilization',
  'linear time-varying systems',
  'nonlinear uncertainties',
  'closed-loop systems',
  'uncertain dynamical systems',
  'state feedback',
  'adaptive controller',
  'robust control',
  'uncertain systems'],
 ['sliding mode control',
  'switching variable',
  'parameter variations',
  'moving switching line',
  'discrete output feedback',
  'fast output sampling feedback',
  'state feedback'],
 ['software simulation',
  'car-based wafer-lot delivery',
  'conveyor-based continuous flow transport technology',
  'automated material handling system',
  'semiconductor fab',
  'throughput',
  'wafer processing',
  'delivery time',
  '300 mm'],
 ['acoustical models',
  'mechanical models',
  'active absorbi

In [34]:
def compareResults(results, keyphrases, n):
    stemmedResults = stemListOfWords(results)
    stemmedKeys = stemListOfWords(keyphrases)
    
    precision = 0
    recall = 0
    fscore = 0
    totalResults = 0
    totalKeyphrases = 0
    correct = 0
    
    n = n
    
    for r in range(len(results)):
        for i in range(n):
            if len(stemmedKeys[r]) > i and stemmedKeys[r][i] in stemmedResults[r]:
                correct += 1
        totalResults += len(stemmedResults[r])
        totalKeyphrases += len(stemmedKeys[r][:n])
        
    precision = correct / totalKeyphrases
    recall = correct / totalResults
    fscore = 2* ((precision * recall)/ (precision + recall))
        
    return precision, recall, fscore, correct, totalResults

In [36]:
def keyPhrasesCompilation(peso, keyWords, g, g2, dicionarioCode,lenght,totalWords):
    key2 = {code : value for code, value in keyWords}
    
    keyphrases_all = []
    
    '''for k in keyWords[:35]:
        for k2 in keyWords[:35]:
            if g2.has_edge(k[0], k2[0]):
                if g2.has_edge(k2[0], k[0]) == False or g2[k2[0]][k[0]]['weight'] < g2[k[0]][k2[0]]['weight']:
                    weight = g.out_degree(k[0], weight='weight') + g.in_degree(k2[0], weight='weight')
                    phrase = [k[0] + ',' + k2[0], g2[k[0]][k2[0]]['weight'], g[k[0]][k2[0]]['weight'] / weight]
                    if phrase not in keyphrases_all:
                        keyphrases_all.append(phrase)
                        
    '''
        
    for k in keyWords[:lenght]:
        for k2 in keyWords[:lenght]:
            if g2.has_edge(k[0], k2[0]) and g2[k[0]][k2[0]]['weight'] >= int(totalWords / 1000) + 2:
                if g2.has_edge(k2[0], k[0]) == False or g2[k2[0]][k[0]]['weight'] < g2[k[0]][k2[0]]['weight']:
                    weight = g.out_degree(k[0], weight='weight') + g.in_degree(k2[0], weight='weight')
                    phrase = [k[0] + ',' + k2[0], g2[k[0]][k2[0]]['weight'], g[k[0]][k2[0]]['weight'] / weight]
                    if phrase not in keyphrases_all:
                        keyphrases_all.append(phrase)
    '''                 
    longer_phrases = []
    for k in keyphrases_all:
        k1 = k[0].split(',')[0]
        k2 = k[0].split(',')[1]
        for key in keyWords[:90]:
            k3 = key[0]
            if g2.has_edge(k2, k3) and g3.has_edge(k1, k3) and g2[k1][k2]['weight'] >= 1 and g3[k1][k3]['weight'] >= 1:
                weight1 = g.out_degree(k1, weight='weight') + g.in_degree(k2, weight='weight')
                #inK1 = g[k1][k3]['weight'] / weight 
                weight2 = g.out_degree(k2, weight='weight') + g.in_degree(k3, weight='weight')
                weight3 = g.out_degree(k1, weight='weight') + g.in_degree(k3, weight='weight')
                #inK2 = g[k2][k3]['weight'] / weight
                #if g3[k1][k3]['weight'] > 0.9 * g2[k2][k3]['weight']:
                phrase = [k1 + ',' + k2 + ',' + k3, 9, ((g[k2][k3]['weight']/weight2) + (g[k1][k2]['weight']/weight3)) ]
                if phrase not in keyphrases_all:
                    longer_phrases.append(phrase)
    keyphrases_all = longer_phrases
    '''
    keyphrases_all = sorted(keyphrases_all, key=lambda kv: (kv[1], kv[0]), reverse=True) 
    #keyphrases_all = keyphrases_all[:6]
    keyphrases_weight = [t[2] for t in keyphrases_all]   # only phrases that appeared more than n times
    keyphrases_weight_norm = [float(i)/sum(keyphrases_weight) for i in keyphrases_weight]
    #keyphrases_weight_norm = [i for i in keyphrases_weight]
    keyphrases = [t for t in keyphrases_all]
    
    for kp, n in zip(keyphrases, keyphrases_weight_norm):
        codes = kp[0].split(',')
        #kp[1] = ((key2[codes[0]] + key2[codes[1]] ) / 2 ) / ((1-(n/(peso[codes[0]] * peso[codes[1]]))) / 1)
        #kp[1] = ((key2[codes[0]] + key2[codes[1]] ) / 2 ) / ((1.000000000000001-(n)))
        kp[1] = ((key2[codes[0]] + key2[codes[1]])) * (n)
        #kp[1] = n 
        #kp[1] = 0.8 * n + 0.2 * ((key2[codes[0]] + key2[codes[1]]) / 2) 
        #kp[1] = ((key2[codes[0]] + key2[codes[1]]) / 2)
        #if len(codes) == 3:
        #    kp[0] = dicionarioCode[codes[0]] + ' ' + dicionarioCode[codes[1]] + ' ' + dicionarioCode[codes[2]]
            #print(kp[0])
        #else:
        
        
        
        
        #M = nx.contracted_nodes(g, codes[0], codes[1])
        #pr = nx.degree_centrality(M)  
        #kp[1] = pr[codes[0]] ** (1/(len(re.split(' |-',dicionarioCode[codes[0]]))+len(re.split(' |-',dicionarioCode[codes[1]]))))
        #print('antes: ' + str(kp[1]))
        #kp[1] = kp[1] / kp[2]
        #kp[1] = (kp[1] / max(g2.nodes()[codes[0]]['peso'],g2.nodes()[codes[1]]['peso'])) * g2[codes[0]][codes[1]]['weight'] #normaliza pelo tanto de aparicoes da frase composta
       
        
        
        
        kp[0] = dicionarioCode[codes[0]] + ' ' + dicionarioCode[codes[1]]
        
    soma = sum([v[1] for v in keyphrases])
    keyphrases = [[k[0], 1* k[1]/soma, k[2]] for k in keyphrases]   
    keywords = [[dicionarioCode[k[0]], k[1], 1] for k in keyWords]    
    merged = keyphrases[:6] + keywords
    #merged = keyphrases
    
    
    
   # for k in merged:
   #     if len(k[0].split(' ')) <= 2:
   #         k[1] = 0
   #         k[0] = 'banana banana'

    
    
    merged.sort(key=takeSecond, reverse=True)
        
    return merged

## Run Experiment

In [50]:
phrases = []
graphs = []
graphs2 = []
graphs3 = []
dit = 3 #testar com 15
words = []

for i in range(500):
    g, g2, g3 = createGraph(peso[i], paragraphs_code[i], dit)
    #g, g2 = mergeNodes(g,g2,dicionarioCode[i])    
    graphs.append(g)
    graphs2.append(g2)
    
    keywords = nodeRank(graphs[i],dicionarioCode[i])    
    
    
    #Exclui verbos no infinitivo
    key2 = []
    for k in keywords:
        #if graphs2[i].nodes[k[0]]['peso'] > 1:
        palavras = dicionarioCode[i][k[0]]
        tokens = nltk.word_tokenize(palavras)
        verb = False
        for w in nltk.pos_tag(tokens):
            if w[1][0] != 'N' and w[1][0] != 'J' and w[1][0] != 'V':# or w[1] == 'VB' or w[1] == 'VBD':
                verb = True
            #if w[1] == 'VB'
            #    verb = True
        if verb:
            bla = [k[0], 0]
            key2.append(bla)

        else:
            key2.append(k)
             
                
    keywords = []
    keywords = key2
    keywords = sorted(keywords, key=lambda kv: (kv[1], kv[0]), reverse=True)     
    
    lenght = int(1*len(keywords))
    soma = sum([v[1] for v in keywords[:lenght]])
    keywords = [[k[0], k[1]/soma] for k in keywords[:lenght]]    
    keywords = [[k[0], (k[1]**(1/(len(dicionarioCode[i][k[0]].split(' ')))))] for k in keywords[:lenght]]
    #keywords = [[k[0], (k[1]**(1/(len(re.split(' |-',dicionarioCode[i][k[0]])))))] for k in keywords[:90]]
    
    keywords = sorted(keywords, key=lambda kv: (kv[1], kv[0]), reverse=True)  
    
    
    firstWords = []
    totalWords = sum([len(i) for i in paragraphs_code[i]])
    
    if totalWords > 1000:
        threshold = int(totalWords * .18)
    else:
        threshold = totalWords
    
    for p in paragraphs_code[i]:
        for w in p:
            if len(firstWords) < threshold:
                firstWords.append(w)
            else:
                break
    
    newKeywords = []
    
    for k in keywords:
        if k[0] in firstWords:
            newKeywords.append(k)
    keywords = newKeywords
    
    
    nodesToRemove = []
    for n in g:
        inKeywords = False
        for k in keywords:
            if k[0] == n:
                inKeywords = True
        if inKeywords == False:
            nodesToRemove.append(n)
            
    for n in nodesToRemove:
        g.remove_node(n)
        g2.remove_node(n)
    
    
    
    #soma = sum([v[1] for v in keywords])
    #keywords = [[k[0], k[1]/soma] for k in keywords]    
    #keywords = [[k[0], 3*(k[1]**(1/(len(dicionarioCode[i][k[0]].split(' ')))))] for k in keywords]
    #for k in keywords:
        #if len(dicionarioCode[i][k[0]].split(' ')) <= 1:
        #    k[1] = 0
    
    
    #Test with just 1 keyword
    #for k in keywords:
    #    if len(dicionarioCode[i][k[0]].split(' ')) > 1:
    #        k[1] = 0
    
    
   # keywords = [[k[0], 1*(k[1]*((len(dicionarioCode[i][k[0]].split(' ')))))] for k in keywords[:90]]
    
    #keywords = [[k[0], (k[1] + ((k[1] * (len(dicionarioCode[i][k[0]].split(' ')) - 1))**(1/3)))] for k in keywords]
    #keywords = [[k[0], (k[1] + 1* (35/(0.000000000000001+sum([1 for t in keywords[:35] if len(dicionarioCode[i][t[0]].split(' ')) == len(dicionarioCode[i][k[0]].split(' '))]))) * k[1])] for k in keywords[:35]]
    words.append(keywords)
    keyphrase = keyPhrasesCompilation(peso[i], keywords,graphs[i],graphs2[i],dicionarioCode[i],lenght,totalWords)    
    phrases.append(keyphrase)
    print(i)
    
keys = []
for p in phrases:
    key = []
    for kp in p:
        key.append(kp[0])
    keys.append(key)

    

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [52]:
compareResults(openResults(),keys,5)

(0.3148, 0.16018725829432118, 0.21232969108323216, 787, 4913)

In [53]:
compareResults(openResults(),keys,10)

(0.2308, 0.2348870343985345, 0.23282558256834457, 1154, 4913)

In [54]:
compareResults(openResults(),keys,15)

(0.17052603399812608, 0.2593120293099939, 0.20574935400516792, 1274, 4913)

In [41]:
openResults()

[['wavelength services',
  'fiber optic networks',
  'Looking Glass Networks',
  'PointEast Research'],
 ['telecom',
  'competitive carrier market',
  'NuVox Communications',
  'investors'],
 ['telecom industry', 'insider investment'],
 ['robust stabilization',
  'adaptive stabilization',
  'linear time-varying systems',
  'nonlinear uncertainties',
  'closed-loop systems',
  'uncertain dynamical systems',
  'state feedback',
  'adaptive controller',
  'robust control',
  'uncertain systems'],
 ['sliding mode control',
  'switching variable',
  'parameter variations',
  'moving switching line',
  'discrete output feedback',
  'fast output sampling feedback',
  'state feedback'],
 ['software simulation',
  'car-based wafer-lot delivery',
  'conveyor-based continuous flow transport technology',
  'automated material handling system',
  'semiconductor fab',
  'throughput',
  'wafer processing',
  'delivery time',
  '300 mm'],
 ['acoustical models',
  'mechanical models',
  'active absorbi

In [62]:
maximum = 0
minimum = 100000000
average = 0
count = 0
for l in openResults():
    for w in l:
        n = len(w.split(' '))
        if n > maximum:
            maximum = n
        if n < minimum:
            minimum = n
            print(w)
        average += n
        count += 1
average = average / count
print(maximum)
print(minimum)
print(average)

wavelength services
telecommunication
9
1
2.214345520513536


In [60]:
openResults()

[['wavelength services',
  'fiber optic networks',
  'Looking Glass Networks',
  'PointEast Research',
  'optical fibre networks',
  'telecommunication'],
 ['telecom',
  'competitive carrier market',
  'NuVox Communications',
  'investors',
  'telecommunication'],
 ['telecom industry', 'insider investment', 'telecommunication'],
 ['robust stabilization',
  'adaptive stabilization',
  'linear time-varying systems',
  'nonlinear uncertainties',
  'closed-loop systems',
  'uncertain dynamical systems',
  'state feedback',
  'adaptive controller',
  'robust control',
  'uncertain systems',
  'adaptive systems',
  'linear systems',
  'robust control',
  'state feedback',
  'time-varying systems',
  'uncertain systems'],
 ['sliding mode control',
  'switching variable',
  'parameter variations',
  'moving switching line',
  'discrete output feedback',
  'fast output sampling feedback',
  'state feedback',
  'state feedback',
  'variable structure systems'],
 ['software simulation',
  'car-ba

In [81]:
[k[:10] for k in keys]

[['wavelength services',
  'live up to',
  'ad nauseam',
  'services',
  'wavelength',
  'industrys',
  'turn-up',
  'confusion',
  'quick',
  'lukewarm'],
 ['long run',
  'new credit',
  'staying power',
  'cash',
  'market',
  'new',
  'says',
  'todays',
  'positions',
  'raise'],
 ['company stock',
  'Crown Castle International',
  'vote of confidence',
  'Cox Communications',
  'Nortel Networks',
  'Charter Communications',
  'Nextel Communications',
  'national economy',
  'insiders',
  'purchasing'],
 ['state feedback control',
  'adaptive robust',
  'state feedback controller',
  'closed-loop systems',
  'feedback control',
  'linear systems',
  'dynamical systems',
  'robust',
  'adaptive',
  'uncertainties'],
 ['output feedback sliding mode control',
  'sliding mode control',
  'second order systems',
  'Discrete output feedback',
  'switching line',
  'make use',
  'initial conditions',
  'output feedback',
  'together with',
  'switching'],
 ['continuous flow',
  'automatio

In [217]:
phrases

[[['ad nauseam years', 0.9830110497304547, 0.2928225532548825],
  ['wavelength services', 0.8539580946293555, 0.2928537149809183],
  ['services ad nauseam', 0.6882766640845585, 0.15421547684560477],
  ['turn-up time', 0.35332436995508243, 0.2928225532548825],
  ['confusion surrounds', 0.35332436995508243, 0.2928225532548825],
  ['quick turn-up', 0.35332436995508243, 0.2928225532548825],
  ['lukewarm reception', 0.35332436995508243, 0.2928225532548825],
  ['impressive margins', 0.35332436995508243, 0.2928225532548825],
  ['surrounds technology', 0.35332436995508243, 0.2928225532548825],
  ['years quick', 0.35332436995508243, 0.2928225532548825],
  ['time impressive', 0.35332436995508243, 0.2928225532548825],
  ['reception confusion', 0.35332436995508243, 0.2928225532548825],
  ['reasons lukewarm', 0.35332436995508243, 0.2928225532548825],
  ['industrys expectations', 0.35332436995508243, 0.195215035503255],
  ['industrys observers', 0.35332436995508243, 0.195215035503255],
  ['expectati

In [184]:
phrases

[[['wavelength services', 0.293809313211875, 0.2928537149809183],
  ['services', 0.17894736842105263, 1],
  ['wavelength', 0.12631578947368421, 1],
  ['industrys', 0.12631578947368421, 1],
  ['turn-up time', 0.1215633309531166, 0.2928225532548825],
  ['confusion surrounds', 0.1215633309531166, 0.2928225532548825],
  ['quick turn-up', 0.1215633309531166, 0.2928225532548825],
  ['years quick', 0.1215633309531166, 0.2928225532548825],
  ['time impressive', 0.1215633309531166, 0.2928225532548825],
  ['convinced wavelength', 0.09837403202254204, 0.15797601137867257],
  ['turn-up', 0.06315789473684211, 1],
  ['confusion', 0.06315789473684211, 1],
  ['quick', 0.06315789473684211, 1],
  ['lukewarm', 0.06315789473684211, 1],
  ['impressive', 0.06315789473684211, 1],
  ['convinced', 0.06315789473684211, 1],
  ['surrounds', 0.06315789473684211, 1],
  ['years', 0.06315789473684211, 1],
  ['time', 0.06315789473684211, 1]],
 [['positions long run', 0.3510657027617531, 0.2928225532548825],
  ['long r

In [86]:
phrases[1]

[['processor speeds', 0.08587447843817951, 1],
 ['grid computing', 0.07271398995795757, 1],
 ['application performance', 0.07271398995795757, 1],
 ['Applications', 0.05523862529567273, 1],
 ['processors', 0.043133435369416995, 1],
 ['resource', 0.03116738555725615, 1],
 ['adaptation', 0.030054264644497, 1],
 ['nodes', 0.026158341449839983, 1],
 ['Grid', 0.02518436065117573, 1],
 ['cluster', 0.022540698483372753, 1],
 ['efficiency', 0.022262418255182964, 1],
 ['performance', 0.020731877000139134, 1],
 ['computing', 0.020592736886044242, 1],
 ['number', 0.018366495060525945, 1],
 ['requirements', 0.017253374147766797, 1],
 ['approach', 0.016696813691387223, 1],
 ['adding', 0.01614025323500765, 1],
 ['overhead', 0.015583692778628075, 1],
 ['removing', 0.015444552664533182, 1],
 ['running', 0.014053151523584247, 1],
 ['runtime', 0.014053151523584247, 1],
 ['scheduling', 0.013218310839014886, 1],
 ['iteration', 0.013079170724919991, 1],
 ['coordinator', 0.01224433004035063, 1],
 ['selection

In [ ]:
indice = 2
for p in phrases[indice]:
    tokens = nltk.word_tokenize(p[0])
    texto = ""
    for w in nltk.pos_tag(tokens):
        print(w)
    
    #for word in tokens:
    #    texto = texto + word + ' ' + 
        #palavras = dicionarioCode[i][k[0]]
        #tokens = nltk.word_tokenize(palavras)
        #for t in tokens:

In [261]:
for w in words[7]:
    print(dicionarioCode[7][w[0]] + ' ' + str(w[1]))

conference 0.17022552783109401
Client 0.11408349328214967
packets 0.11192418426103645
domain 0.09788867562380038
number 0.08745201535508637
Conferencing 0.08709213051823414
streams 0.07593570057581572
CSs 0.06261996161228404
networks 0.06118042226487523
Servers 0.0593809980806142
SIP 0.05074376199616122
mixing 0.05002399232245681
selected 0.04858445297504798
LN 0.04570537428023032
placed 0.0446257197696737
presented 0.04354606525911707
sends 0.04174664107485604
traffic 0.040307101727447205
CS 0.03994721689059501
Algorithms 0.03994721689059501
application 0.03742802303262955
audio 0.036708253358925136
Fig 0.036708253358925136
speakers 0.03562859884836852
case 0.03562859884836852
time 0.03310940499040307
participants 0.03310940499040307
VoIP 0.03202975047984644
reduce 0.03166986564299423
handling 0.03023032629558541
framework 0.03023032629558541
Issues 0.02951055662188099
bandwidth 0.02951055662188099
active 0.02915067178502878
rms 0.028071017274472164
System 0.026631477927063336
differe

In [ ]:
def saveKeyWords(keyWords, graphName, resultFile):
    file = open(resultFile,"w+") 
    stemmer=PorterStemmer()
    for words, name in zip(keyWords, graphName):
        file.write(name + " : ")
        #for word in [it[0] for it in nltk.pos_tag([item[0] for item in words]) if it[1] != 'VBN'][:15]:
        for word, weight, weight2 in words[:15]:
            parsedPhrase = ''
            count = 0
            for w in word.split(' '):
                if w != '':
                    parsedWord = stemmer.stem(w.lower())
                    count = count + 1
                    if count > 1:
                        parsedPhrase = parsedPhrase + ' ' + parsedWord
                    else:
                        parsedPhrase = parsedWord

            if(word != words[0][0]):
                file.write("," + parsedPhrase)
            else:
                file.write(parsedPhrase)
        file.write("\n")
    file.close()
    return 

In [259]:
count = 0
for k in words[7]:
    count = count + 1
    print(str(count) + '\t' + dicionarioCode[3][k[0]] + '\t' + str(k[1]))

1	Conference	0.17022552783109401
2	client	0.11408349328214967


KeyError: 'bn:00013882n'

In [ ]:
stemmer=PorterStemmer()


In [ ]:
peso[0]['bn:00819565n']

In [ ]:
graphs[0].node('bn:03664545n', weight=True)

In [ ]:
dicionarioCode[0]['bn:03664545n']

In [ ]:
dicionario[0]['UDDI']

In [ ]:
graphs2[0]['bn:00041777n']['bn:00395755n']

In [ ]:
graphs2[0].has_edge('bn:00102206a', 'bn:00036197n')

In [ ]:
for u, v, weight in graphs[0].edges(data='weight'):
    if u == 'bn:00070651n' and weight > 5 and u != v:
        print(dicionarioCode[0][v] + ' ' + str(weight))

In [131]:
len(paragraphs_annotations)

408

# Babelfy text

In [45]:
#key = "993c40dd-2a16-45f3-89c6-67b47824b9da" 
key = "3e33574f-d481-41ae-82f1-0a7caf846dd3" 

In [54]:
graphName = []
splitted_text = []
dicionario = []
dicionarioCode = []
peso = []
paragraphs_annotations = []
paragraphs_text = []
paragraphs_code = []
graphs = []
graphs2 = []
keyWords = []
keyPhrases = []
inputDirectory = "/home/mauro/Downloads/Hulth2003/Test/Abstr/"


In [57]:
def startDownload():
    count = 0
    atual = 496
    for filename in sorted(glob.glob(os.path.join(inputDirectory, '*.abstr')), key=numericalSort):
        if count >= atual:
            graphName.append(filename[43:-6])
            text = openFile(filename) 
            st = parseText(text)
            splitted_text.append(st)
            
            pa, pt, pc  = babelfy(lang, key, st)
            paragraphs_annotations.append(pa)
            paragraphs_text.append(pt)
            paragraphs_code.append(pc)
            #saveText(saveFile, paragraphs_code)

            d, dc, p = createDicts(pt, pc)
            dicionario.append(d)
            dicionarioCode.append(dc)
            peso.append(p)
        count = count + 1
        print('Artigo: ' + str(count))


## Run download in background

In [58]:
import threading

In [59]:
thr = threading.Thread(target=startDownload, args=())

In [60]:
thr.daemon = True

In [61]:
thr.start()

Artigo: 1
Artigo: 2
Artigo: 3
Artigo: 4
Artigo: 5
Artigo: 6
Artigo: 7
Artigo: 8
Artigo: 9
Artigo: 10
Artigo: 11
Artigo: 12
Artigo: 13
Artigo: 14
Artigo: 15
Artigo: 16
Artigo: 17
Artigo: 18
Artigo: 19
Artigo: 20
Artigo: 21
Artigo: 22
Artigo: 23
Artigo: 24
Artigo: 25
Artigo: 26
Artigo: 27
Artigo: 28
Artigo: 29
Artigo: 30
Artigo: 31
Artigo: 32
Artigo: 33
Artigo: 34
Artigo: 35
Artigo: 36
Artigo: 37
Artigo: 38
Artigo: 39
Artigo: 40
Artigo: 41
Artigo: 42
Artigo: 43
Artigo: 44
Artigo: 45
Artigo: 46
Artigo: 47
Artigo: 48
Artigo: 49
Artigo: 50
Artigo: 51
Artigo: 52
Artigo: 53
Artigo: 54
Artigo: 55
Artigo: 56
Artigo: 57
Artigo: 58
Artigo: 59
Artigo: 60
Artigo: 61
Artigo: 62
Artigo: 63
Artigo: 64
Artigo: 65
Artigo: 66
Artigo: 67
Artigo: 68
Artigo: 69
Artigo: 70
Artigo: 71
Artigo: 72
Artigo: 73
Artigo: 74
Artigo: 75
Artigo: 76
Artigo: 77
Artigo: 78
Artigo: 79
Artigo: 80
Artigo: 81
Artigo: 82
Artigo: 83
Artigo: 84
Artigo: 85
Artigo: 86
Artigo: 87
Artigo: 88
Artigo: 89
Artigo: 90
Artigo: 91
Artigo: 

In [64]:
thr.is_alive()

False

In [65]:
len(splitted_text)

500

In [66]:
len(paragraphs_annotations)

500

In [54]:
#splitted_text.pop(496)
#graphName.pop(496)

'2192'

# Save babelfyed text

In [51]:
saveFile = '/home/mauro/Documentos/Mestrado/babelfyLists/'

In [67]:
'''
with open(saveFile + "graphNameInspec.pickle", "wb") as fp:
    pickle.dump(graphName, fp)
with open(saveFile + "splitted_textInspec.pickle", "wb") as fp:
    pickle.dump(splitted_text, fp)
with open(saveFile + "dicionarioInspec.pickle", "wb") as fp:
    pickle.dump(dicionario, fp)
with open(saveFile + "dicionarioCodeInspec.pickle", "wb") as fp:
    pickle.dump(dicionarioCode, fp)
with open(saveFile + "pesoInspec.pickle", "wb") as fp:
    pickle.dump(peso, fp)
with open(saveFile + "paragraphs_annotationsInspec.pickle", "wb") as fp:
    pickle.dump(paragraphs_annotations, fp)
with open(saveFile + "paragraphs_textInspec.pickle", "wb") as fp:
    pickle.dump(paragraphs_text, fp)
with open(saveFile + "paragraphs_codeInspec.pickle", "wb") as fp:
    pickle.dump(paragraphs_code, fp)
'''
with open(saveFile + "graphsDist4Inspec.pickle", "wb") as fp:
    pickle.dump(graphs, fp)
with open(saveFile + "graphs2Dist4Inspec.pickle", "wb") as fp:
    pickle.dump(graphs2, fp)

## Open babelfyed text

In [39]:

graphName = []
splitted_text = []
dicionario = []
dicionarioCode = []
peso = []
paragraphs_annotations = []
paragraphs_text = []
paragraphs_code = []
graphs = []
graphs2 = []
keyWords = []
keyPhrases = []
inputDirectory = "/home/mauro/Downloads/Hulth2003/Test/Abstr/"
saveFile = '/home/mauro/Documentos/Mestrado/babelfyLists/'

with open (saveFile + "graphNameInspec.pickle", 'rb') as fp:
    graphName = pickle.load(fp)
with open (saveFile + "splitted_textInspec.pickle", 'rb') as fp:
    splitted_text = pickle.load(fp)
with open (saveFile + "dicionarioInspec.pickle", 'rb') as fp:
    dicionario = pickle.load(fp)
with open (saveFile + "dicionarioCodeInspec.pickle", 'rb') as fp:
    dicionarioCode = pickle.load(fp)
with open (saveFile + "pesoInspec.pickle", 'rb') as fp:
    peso = pickle.load(fp)
with open (saveFile + "paragraphs_annotationsInspec.pickle", 'rb') as fp:
    paragraphs_annotations = pickle.load(fp)
with open (saveFile + "paragraphs_textInspec.pickle", 'rb') as fp:
    paragraphs_text = pickle.load(fp)
with open (saveFile + "paragraphs_codeInspec.pickle", 'rb') as fp:
    paragraphs_code = pickle.load(fp)
#with open (saveFile + "graphsDist3Inspec.pickle", 'rb') as fp:
#    graphs = pickle.load(fp)
#with open (saveFile + "graphs2Dist3Inspec.pickle", 'rb') as fp:
#    graphs2 = pickle.load(fp)

In [124]:
graphName = []
splitted_text = []
dicionario = []
dicionarioCode = []
peso = []
paragraphs_annotations = []
paragraphs_text = []
paragraphs_code = []
graphs = []
graphs2 = []
keyWords = []
keyPhrases = []